In [1]:
from __future__ import print_function
from functools import reduce
import re
from nltk.tokenize import word_tokenize
from keras.utils.data_utils import get_file
from keras.layers.embeddings import Embedding
from keras import layers
from keras.layers import recurrent, Bidirectional, Dense, Flatten
from keras.models import Model
from keras.preprocessing.sequence import pad_sequences
from keras import backend as K
from keras.models import load_model
import json
from pprint import pprint
import numpy as np
import csv
import string

Using TensorFlow backend.


In [2]:

def get_dictionary(vocab):
    d = dict()
    with open(vocab) as f:
        lines = f.readlines()
        for l in lines:
            values = l.strip().split()
            word = values[0]
            coefs = np.asarray(values[1:], dtype='float32')
            d[word] = coefs
    return d

In [3]:
d = get_dictionary("glove/glove.6B.300d.txt")

In [4]:
def normalize_answer(s):
    """Lower text and remove punctuation, articles and extra whitespace."""
    def remove_articles(text):
        return re.sub(r'\b(a|an|the)\b', ' ', text)

    def white_space_fix(text):
        return ' '.join(text.split())

    def remove_punc(text):
        exclude = set(string.punctuation)
        return ''.join(ch for ch in text if ch not in exclude)

    def lower(text):
        return text.lower()
    
    return white_space_fix(remove_articles(remove_punc(lower(s))))

In [83]:
with open('train.json') as data_file:    
    data = json.load(data_file)

In [84]:
ids = []
titles = dict()
contexts = dict()
questions = dict()
answers_text = dict()
answers_start = dict()
for i in range(len(data)):
    paragraphs = data[i]["paragraphs"]
    title = data[i]["title"]
    for j in range(len(paragraphs)):
        context = paragraphs[j]["context"]
        qas = paragraphs[j]["qas"]
        for k in range(len(qas)):
            answer = qas[k]["answer"]
            id_ = qas[k]["id"]
            question = qas[k]["question"]
            ids.append(id_)
            titles[id_] = title
            contexts[id_] = context
            questions[id_] = question
            answers_start[id_] = answer["answer_start"]
            answers_text[id_] = answer["text"]

In [85]:
max_para = 600
max_q = 50
dimension = 300

In [153]:
test_len = 5000

In [154]:
paras = np.zeros((test_len, max_para, dimension))
qns = np.zeros((test_len, max_q, dimension))


# In[14]:

for i in range(test_len):
    words = word_tokenize(contexts[ids[i]].lower())
    qs = word_tokenize(questions[ids[i]].lower())
    for j in range(min(max_para - 1, len(words))):
        if words[j] in d:
            paras[i][j] = d[words[j]]
    for j in range(min(max_q - 1, len(qs))):
        if qs[j] in d:
            qns[i][j] = d[qs[j]]

In [112]:
model = load_model('model_3')

/Users/duynguyen/anaconda/lib/python3.5/site-packages/keras/models.py:287: UserWarning: Error in loading the saved optimizer state. As a result, your model is starting with a freshly initialized optimizer.
  warnings.warn('Error in loading the saved optimizer '


In [156]:
out = model.predict([paras,qns])

In [157]:
out_1 = np.argmax(out[0], axis=1)
out_2 = np.argmax(out[1], axis=1)

In [158]:
def search(para, pos):
    word_list = word_tokenize(para)
    s = ''.join(word_list[:pos])
    if pos == 0: 
        return 0
    if len(word_list) <= pos:
        return len(para)
    else:
        begin, end = 0, len(para)
        while begin < end:
            mid = (begin + end) // 2
            a = word_tokenize(para[:mid])
            s_ = ''.join(a)
            if (len(s_) < len(s)):
                begin = mid + 1
            elif (len(s_) > len(s)):
                end = mid
            elif s == s_:
                break
        return mid
          

In [159]:
for i in range(test_len):
    s = 0
    t = 1
    if i%1000 == 0: 
        print(i)
    for j in range(max_para):
        for k in range(j, min(j+10, max_para)):
            if out[0][i][s] * out[1][i][t] < out[0][i][j] * out[1][i][k]:
                s = j
                t = k
    out_1[i] = s
    out_2[i] = t
#     print(s, t)

0
1000
2000
3000
4000


In [160]:
out_2 = out_2 + 1

In [162]:
c = 0
for i in range(5000):
    a = search(contexts[ids[i]], out_1[i])
    b = search(contexts[ids[i]], out_2[i])
    print(ids[i])
    print(contexts[ids[i]])
    print("\n")
    print(questions[ids[i]])
    print("\n")
    print(normalize_answer(contexts[ids[i]][a:b]))
    print("\n")
    print(normalize_answer(answers_text[ids[i]]))
    print("------------")
    if normalize_answer(contexts[ids[i]][a:b]) == normalize_answer(answers_text[ids[i]]):
        c += 1
    

000000
In 1790, the first federal population census was taken in the United States. Enumerators were instructed to classify free residents as white or "other." Only the heads of households were identified by name in the federal census until 1850. Native Americans were included among "Other;" in later censuses, they were included as "Free people of color" if they were not living on Indian reservations. Slaves were counted separately from free persons in all the censuses until the Civil War and end of slavery. In later censuses, people of African descent were classified by appearance as mulatto (which recognized visible European ancestry in addition to African) or black.


When was the first federal population census taken in the US?


1790


1790
------------
000001
In 1790, the first federal population census was taken in the United States. Enumerators were instructed to classify free residents as white or "other." Only the heads of households were identified by name in the federal cen

In [163]:
print(c/5000)

0.8112


In [37]:
with open("submission_2.csv", 'w') as f:
    writer = csv.writer(f, delimiter=',')
    writer.writerow(['Id','Answer'])
    for i in ind:
        a = search(contexts[ids[i]], out_1[i])
        b = search(contexts[ids[i]], out_2[i])
        writer.writerow([ids[i],normalize_answer(contexts[ids[i]][a:b])])
        print(i)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27